## Web Crawler Module

In [1]:
#Importing the necessary packages
from selenium import webdriver
from bs4 import BeautifulSoup
import pandas as pd
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
import random,time
import requests
from nordvpn_switcher import initialize_VPN,rotate_VPN,terminate_VPN
from fake_useragent import UserAgent
from selenium.webdriver.common.desired_capabilities import DesiredCapabilities
initialize_VPN(save=1,area_input=['complete rotation'])
import warnings
import pickle
from snowballstemmer import EnglishStemmer as es
from nltk.corpus import stopwords
import re
warnings.filterwarnings('ignore')
prof_list = []
counter = 0

You're using Windows.
Performing system check...
###########################

NordVPN installation check: ✓
NordVPN service check: ✓
Opening NordVPN app and disconnecting if necessary...
NordVPN app launched: ✓
#####################################

You've entered a list of connection options. Checking list...


Fetching list of all current NordVPN servers...


Saving settings in project folder...


Done!



In [2]:
#********************************************************
#Method to get profile details
def get_Author_Profiles(page):
    s = BeautifulSoup(page, "html.parser")
    #print(s.find_all_next('h3'))
    for link in s.findAll('h3'):
        a_link = link.findAll('a')
        prof_list.append("https://scholar.google.co.uk"+link.findAll('a')[0].get('href'))
        #print("----------------------------")
#Method to fetch paper details
def get_paper_deails(paper):
    global counter
    #counter+=1
    #adding sleeptime
    time.sleep(random.uniform(0,random.uniform(3,8)))
    dcap = dict(DesiredCapabilities.PHANTOMJS)
    dcap["phantomjs.page.settings.userAgent"] = (UserAgent().random)
    dr = webdriver.PhantomJS(executable_path='D:\\phantomjswindows\\bin\\phantomjs', desired_capabilities=dcap)
    while True:
        dr.get(paper)
        #adding sleep time
        time.sleep(random.uniform(1.5,3))
        if "www.google.com/sorry/" not in dr.current_url:
            break
        print("Current IP blocked. Rotating IP")
        rotate_VPN()
    #print(dr.current_url)
    s_research = BeautifulSoup(dr.page_source, "html.parser")
    paper_auth =  s_research.find(class_ = 'gsc_vcd_value').contents[0]
    paper_link = s_research.find(class_ = 'gsc_vcd_title_link').get('href')
    paper_title = s_research.find(class_ = 'gsc_vcd_title_link').contents[0]
    return paper_title,paper_auth,paper_link


In [3]:
#crawls throgh every profiles and fetches their paper details in BFS manner
def my_Crawler(prof_list):
    titles= []
    links =[]
    auths =[]
    fail=[]
    papers_tmp =[]
    baseurl = "https://scholar.google.co.in/"
    count_prof = 0
    #iterating through the profile links
    for prof in prof_list:
        driver = webdriver.PhantomJS(executable_path='D:\\phantomjswindows\\bin\\phantomjs')
        while True:
            driver.get(prof)
            if "www.google.com/sorry/" not in driver.current_url:
                break
            print("rotating IP")
            rotate_VPN()
        wait = WebDriverWait(driver, 10)
        while True:
            try:
                #adding sleep time
                time.sleep(random.uniform(3,random.uniform(4,7)))
                element = wait.until(EC.element_to_be_clickable((By.ID, 'gsc_bpf_more')))
                element.click()
            except TimeoutException:
                break
        papers = []
        s = BeautifulSoup(driver.page_source, "html.parser")
        for paper in s.findAll('a', class_="gsc_a_at"):
            papers.append(baseurl+paper.get('data-href'))
        print("Found {} papers of profile {}".format(len(papers),count_prof+1))
        #iterating through the paper link of profiles
        for p in papers:
            if p not in papers_tmp:
                try:
                    #print(p)
                    paper_title,paper_auth,paper_link = get_paper_deails(p)
                    titles.append(paper_title)
                    links.append(paper_link)
                    auths.append(paper_auth)
                except:
                    fail.append(p)
                    #print("Error with link: {}".format(p))
                papers_tmp.append(p)
            #print(paper_link)
        #df_tmp = pd.DataFrame({'title':titles, 'auth':auths,'link':links})
        #df_tmp.to_csv("tmp_papers.csv")
        count_prof+=1
        print("Done..! profile {} with {}".format(count_prof,len(papers)))
        driver.quit()
#     if len(fail)>0:
#         df_fail = pd.DataFrame({'link':fail})
#         df_tmp.to_csv("tmp_papers.csv")
    df_papers = pd.DataFrame({'title':titles, 'auth':auths,'link':links})
    return df_papers
#to fetch the profiles into profiles fils
def crawler_profiles():
    driver_prof = webdriver.PhantomJS(executable_path='D:\\phantomjswindows\\bin\\phantomjs')
    driver_prof.get('https://scholar.google.co.uk/citations?view_op=view_org&hl=en&org=9117984065169182779')
    button = driver_prof.find_elements_by_css_selector("[aria-label=Next]")
    titles= []
    links =[]
    auths =[]
    baseurl = "https://scholar.google.co.in/"
    count_prof = 0
    get_Author_Profiles(driver_prof.page_source)
    print(driver_prof.current_url)
    while True:
        button = driver_prof.find_elements_by_css_selector("[aria-label=Next]")
        url_temp = driver_prof.current_url
        time.sleep(random.uniform(0,random.uniform(0,10)))
        button[0].click()
        if url_temp==driver_prof.current_url:
            break
        get_Author_Profiles(driver_prof.page_source)
    print("Done! Profiles:",len(prof_list))
    driver_prof.close()

In [4]:

#********************************************************

# Inverted index

In [5]:
#Stop words
englishStopWords = stopwords.words('english')


In [6]:
# function for text cleaning 
def clean_text(text):
    # remove backslash-apostrophe 
    text = re.sub("\':.", "", text) 
    # remove everything except alphabets 
    text = re.sub("[^a-zA-Z]"," ",text) 
    # remove whitespaces 
    text = ' '.join(text.split()) 
    # convert text to lowercase 
    text = text.lower() 
    return text
def clean(data):
    data = clean_text(data) #cleaning the data
    words = data.split()
    words = [word.lower() for word in words] # changing to lower case
    #print(words)
    words = [es().stemWord(word) for word in words] # Stemming word
    words = [word for word in words if word not in englishStopWords] # Remove stop words
    return words

#Method to create inverted index
def indexer(file, words, index):
    for position in range(len(words)):
        word = words[position]     
        # If the word is not in the index
        if words[position] not in index:
            index[word] = {'term frequency' : 1,
                           'document frequency' : 1,
                           'document(s)' : {file : {'frequency' : 1,
                                                  'position(s)' : [position]}}}
        # If the word is in the index
        else:
            index[word]['term frequency'] += 1
            if file not in index[word]['document(s)']: # If the word not found
                index[word]['document frequency'] += 1
                index[word]['document(s)'][file] = {'frequency' : 1,
                                                  'position(s)' : [position]}
            else: # If the word found in this document
                 index[word]['document(s)'][file]['frequency'] += 1
                 index[word]['document(s)'][file]['position(s)'].append(position)
    return index


In [7]:
def main_indexer():
    #loading the scrawled data
    data = pd.read_csv("data.csv")
    #combining the paper titles and authr details to include authors in the search engine logic
    data['text'] = data['title'].str.cat(data['auth'],sep=" ")
    index = {}
    # Iterate through every file
    i = 0
    for dt in data["text"]:
        #cleaning the data
        words = clean(dt)
        name = i
        # Add the words to the index
        #print(words)
        indexer(name, words, index)
        i+=1
    pickle_out = open("indexer.pickle","wb")
    pickle.dump(index, pickle_out)
    print("Inverted Indexing Done!")
    return index

In [8]:
#method to start the crawler
def start_crawler():
    crawler_profiles()
    df_prof_list = pd.read_csv("Profiles.csv")
    df_papers = my_Crawler(df_prof_list["link"])
    df_papers.to_csv("data.csv")
    index= main_indexer() #creating inverted index after crawling is done
    #writing the settings flag to notify the flask app
    settings = pd.DataFrame({'time':[time.time], 'flag':["Done"]})
    settings.to_csv("settings.csv")


In [9]:
start_crawler() #Initial run
#starting the craler
import schedule
import time
# Every monday crawler is called
schedule.every(10).days.do(start_crawler)
while True:
    schedule.every()
    time.sleep(1)

Found 5 papers of profile 1
Done..! profile 1 with 5
Found 3 papers of profile 2
Done..! profile 2 with 3
Found 1 papers of profile 3
Done..! profile 3 with 1
Found 4 papers of profile 4
Done..! profile 4 with 4
Found 1 papers of profile 5
Done..! profile 5 with 1
Found 1 papers of profile 6
Done..! profile 6 with 1
Found 5 papers of profile 7
Done..! profile 7 with 5
Found 8 papers of profile 8
Done..! profile 8 with 8
Found 1 papers of profile 9
Done..! profile 9 with 1
Found 1 papers of profile 10
Done..! profile 10 with 1
Found 2 papers of profile 11
Done..! profile 11 with 2
Found 1 papers of profile 12
Done..! profile 12 with 1
Found 1 papers of profile 13
Done..! profile 13 with 1
Found 3 papers of profile 14
Done..! profile 14 with 3
Found 3 papers of profile 15
Done..! profile 15 with 3
Found 3 papers of profile 16
Done..! profile 16 with 3
Found 1 papers of profile 17
Done..! profile 17 with 1
Found 1 papers of profile 18
Done..! profile 18 with 1
Found 1 papers of profile 19

KeyboardInterrupt: 

Below code is for deployment purpose

In [ ]:
# from math import log, sqrt
# from snowballstemmer import EnglishStemmer as es
# from nltk.corpus import stopwords
# import re
# import pickle
# import pandas as pd
# import random,time
# #load vectorizer
# file = open("indexer.pickle",'rb')
# index = pickle.load(file)
# file.close()
# # function for text cleaning 
# def clean_text(text):
#     # remove backslash-apostrophe 
#     text = re.sub("\':.", "", text) 
#     # remove everything except alphabets 
#     text = re.sub("[^a-zA-Z]"," ",text) 
#     # remove whitespaces 
#     text = ' '.join(text.split()) 
#     # convert text to lowercase 
#     text = text.lower() 
#     return text
# #method to clean the query
# def cleanQuery(string):
#     englishStopWords = stopwords.words('english')
#     string= clean_text(string)
#     words = string.split()
    
#     words = [word.lower() for word in words]
#     words = [es().stemWord(word) for word in words]
    
#     words = [word for word in words if word not in englishStopWords]
    
#     return words
# #method to rank using TF-IDF metric
# def rank_Documents(index, words,doc_count):
#     rankings = {}
#     for word in words:
#         doc_freq = index[word]['document frequency']
#         for document in index[word]['document(s)'].keys():
#             TF = index[word]['document(s)'][document]['frequency']
#             IDF = log(doc_count/doc_freq)
#             if TF > 0:
#                 TF = 1 + log(TF)
#             else:
#                 TF = 0
#             if document not in rankings:
#                 rankings[document] = TF*IDF
#             else:
#                 rankings[document] += TF*IDF
#     #sorting the results
#     rankings = list(reversed(sorted(rankings.items(), key=lambda x: x[1])))
#     return rankings
# def get_index_data(idx):
#     return index[idx]
# def do_Search(user_input):
#     words = cleanQuery(user_input)
#     unknown_words = []
#     # Collect the information for each word of the query
#     query_index = {}
#     doc_count = []
#     for word in words:
#         try:
#             query_index[word] = get_index_data(word)
#             doc_count = doc_count + list(index[word]['document(s)'].keys())
#         except:
#             unknown_words.append(word)
#     # Rank the documents according to the query
#     for w in words:  # iterating on a copy since removing will mess things up
#         if w in unknown_words:
#             words.remove(word)
#     results = rank_Documents(query_index, words,len(set(doc_count)))
#     #print(len(set(doc_count)))
#     return results
# #initialising list for final result
# # titles=[]
# # auths=[]
# # links=[]
# # data = pd.read_csv("data.csv")
# # #Doing the query processing
# # for doc, score in do_Search("Timothy James Mason"):
# #     titles.append(data.iloc[doc,0])
# #     auths.append(data.iloc[doc,1])
# #     links.append(data.iloc[doc,2])
# # result_df = pd.DataFrame({'title':titles, 'auth':auths,'link':links})
# # result_df

In [11]:
index = main_indexer()

Inverted Indexing Done!


In [12]:
index

{'sonochemistri': {'term frequency': 71,
  'document frequency': 70,
  'document(s)': {0: {'frequency': 1, 'position(s)': [0]},
   1: {'frequency': 1, 'position(s)': [1]},
   3: {'frequency': 1, 'position(s)': [1]},
   7: {'frequency': 1, 'position(s)': [1]},
   8: {'frequency': 1, 'position(s)': [0]},
   13: {'frequency': 1, 'position(s)': [1]},
   15: {'frequency': 1, 'position(s)': [1]},
   20: {'frequency': 1, 'position(s)': [0]},
   21: {'frequency': 1, 'position(s)': [0]},
   24: {'frequency': 1, 'position(s)': [1]},
   29: {'frequency': 1, 'position(s)': [0]},
   37: {'frequency': 1, 'position(s)': [0]},
   39: {'frequency': 1, 'position(s)': [0]},
   46: {'frequency': 1, 'position(s)': [1]},
   56: {'frequency': 1, 'position(s)': [0]},
   59: {'frequency': 1, 'position(s)': [1]},
   67: {'frequency': 1, 'position(s)': [0]},
   69: {'frequency': 1, 'position(s)': [0]},
   76: {'frequency': 1, 'position(s)': [0]},
   91: {'frequency': 1, 'position(s)': [1]},
   108: {'frequency':

In [17]:

data = pd.read_csv("data.csv")


'Effect of ultrasound treatment on solubility and foaming properties of whey protein suspensions'

In [31]:
print("Data Before cleaning:")
data["title"][7]

Data Before cleaning:


'Quantifying sonochemistry: casting some light on a ‘black art’'

In [32]:
print("Data input to the indexer after cleaning:")
clean(data["title"][7])

Data input to the indexer after cleaning:


['quantifi', 'sonochemistri', 'cast', 'light', 'black', 'art']